### 0. Import libraries and read data

In [137]:
import copy
import json
import tqdm
from itertools import groupby
from operator import itemgetter
from flair.data import Sentence


In [3]:
def read_data(input_file_path):
    data = []

    with open(input_file_path) as f:
        for line in f:
            data.append(json.loads(line))

    return data

In [4]:
def write_data(output_file_path, data):
    # Open a new JSON file for writing
    with open(output_file_path, "w") as output_file:
        for data_line in data:
            output_file.write(json.dumps(data_line) + "\n")

In [5]:
data = read_data("../../data/squad_data_train_pos_ner_agg.json")

In [237]:
NER_TAGS = ['[LOC]', '[MISC]', '[ORG]', '[PER]']

### 1. Find the token index where the answer starts

In [6]:
def is_subustring_in_string(string, substring, symbols):
    for symbol in symbols:
        if symbol in string and (substring in string or substring.replace(" ", "") in string.replace(" ", "")):
           return True
        
    return False

def is_one_text_in_context(text, context, symbols):
    count = 0

    for symbol in symbols:
        if context.count(text + symbol):
            count += 1

    return count == 1

In [7]:
def find_start_position(text, pos_context, answer, context):
    tokens = []
    sentence = Sentence(text)
    symbols = [" ", ")", "(", "%", "-", ".", ","]

    # get how many spaces are until the start position
    spaces_no = context[:answer].count(" ")

    # get tokens of the answer
    for word in sentence:
        tokens.append(word.text)

    start_position = 0
    token_number = 0
    match = False
    no_match = -1

    # check if the answer appear only once
    one_apperance = is_one_text_in_context(text, context, symbols)

    # iterate over positions in the pos context
    for start_position in range(len(pos_context) - len(tokens) + 1):
        # store in k_words_context_ and k_words_context the span of tokens from pos_context
        k_words_context_ = [
            bytes(list(line.values())[0][0], "utf-8").decode("unicode_escape")
            for line in pos_context[start_position : start_position + len(tokens)]
        ]

        k_words_context = [
            list(line.values())[0][0].replace("\\", "")
            for line in pos_context[start_position : start_position + len(tokens)]
        ]

        # get the next word after the context
        next_word = [
            list(line.values())[0][0]
            for line in pos_context[
                start_position + len(tokens) : start_position + len(tokens) + 1
            ]
        ]


        # join all words in a string
        k_words_context_string = " ".join(k_words_context)
        k_words_context_string_ = " ".join(k_words_context_)

        # define exact mach condition
        exact_match = k_words_context == tokens or k_words_context_ == tokens


        # if there is only one appearence and the answer was found, stop
        if context.count(text) == 1 and exact_match:
            match = True
            break

        # if there is only one appearence with the answer followed by a token, stop
        if one_apperance and (
            exact_match
            or is_subustring_in_string(k_words_context_string, text, symbols)
            or is_subustring_in_string(k_words_context_string_, text, symbols)
        ):
            match = True
            break

        # if the occurence is not the first one, but the start position is correct, stop
        if (
            text in k_words_context_string
            or text in k_words_context_string_
            or exact_match
            or is_subustring_in_string(k_words_context_string, text, symbols)
            or is_subustring_in_string(k_words_context_string_, text, symbols)
        ) and (
            token_number + spaces_no == answer or token_number + spaces_no + 1 == answer or token_number + spaces_no - 1 == answer
        ):
            match = True
            break

        # else consider the next word
        elif next_word in symbols and (token_number + spaces_no == answer or token_number + spaces_no + 1 == answer or token_number + spaces_no - 1 == answer):
            no_match = start_position
            break

        if "'" in k_words_context_:
            token_number += len(k_words_context_[0])
        else:
            token_number += len(k_words_context[0])

    if match:
        return start_position
    
    return no_match


In [8]:
def check_start_answer_detection(data):
    incorrect_lines_indices = []
    
    for i, line in tqdm.tqdm(enumerate(data)):
        original_answer = line["answers"]["text"][0]
        original_answer_start = line["answers"]["answer_start"][0]
        original_answer_list = [token.text for token in list(Sentence(original_answer))]

        index = find_start_position(original_answer, line["POS_context"], original_answer_start, line["context"])
        found_answer = [list(token.values())[0][0] for token in line['POS_context'][index:index+len(original_answer_list)]]

        if not " ".join(found_answer).startswith(" ".join(original_answer_list)):
            incorrect_lines_indices.append(i)

    return incorrect_lines_indices

In [9]:
incorrect_lines_indices = check_start_answer_detection(data)
len(incorrect_lines_indices)

0it [00:00, ?it/s]

87599it [01:13, 1185.53it/s]


398

In [10]:
for incorrect_index in incorrect_lines_indices:
    line = data[incorrect_index]
    
    original_answer = line["answers"]["text"][0]
    original_answer_start = line["answers"]["answer_start"][0] 
    original_answer_list = [token.text for token in list(Sentence(original_answer))]

    index = find_start_position(original_answer, line["POS_context"], original_answer_start, line["context"])
    found_answer = [list(token.values())[0][0] for token in line['POS_context'][index:index+len(original_answer_list)]]

    print(original_answer_list, found_answer, index)

['Father', 'Joseph', 'Carrier', ',', 'C.S.C', '.'] ['Father', 'Joseph', 'Carrier', ',', 'C.S.C.', 'was'] 0
['Rev', '.', 'John', 'J.', 'Cavanaugh', ',', 'C.S.C', '.'] ['The', 'Rev', '.', 'John', 'J.', 'Cavanaugh', ',', 'C.S.C.'] 0
['five', '.'] ['top-five', '.'] 149
['Jay', 'Z', '.'] ['married', 'Jay', 'Z.'] 7
["'", '03', 'Bonnie', '&', 'Clyde'] ['"\'', '03', 'Bonnie', '&', 'Clyde'] 16
['B.I.C', '.'] ['"', 'B.I.C.'] 91
['B.I.C', '.'] ['"', 'B.I.C.'] 91
['50'] [] -1
['J.', 'S.', 'Bach', ',', 'Mozart', 'and', 'Schubert'] [] -1
['J.', 'S.', 'Bach', ',', 'Mozart', 'and', 'Schubert'] [] -1
['J.', 'S.', 'Bach', ',', 'Mozart', 'and', 'Schubert'] [] -1
['7'] [] -1
['7'] [] -1
['7'] [] -1
['Rondo', 'Op', '.', '1', '.'] ['his', 'Rondo', 'Op', '.', '1.'] 162
['the', 'Canuts', '.'] [',', 'the', 'Canuts.'] 42
['J.S', '.', 'Bach', "'s", 'The', 'Well-Tempered', 'Clavier'] ['by', 'J.S.', 'Bach', "'s", 'The', 'Well-Tempered', 'Clavier'] 38
['Op', '.', '58'] [',', 'Op.', '58'] 18
['Tibet'] ['Sino-Tibetan

- 106 answers that were not found at all
- 292 answers that were found but a bit different


### 2. Insert NER in the context

In [270]:
errors = 0

for line_index, line in tqdm.tqdm(enumerate(data)):
    """
    Find start index for answer
    """
    original_answer = line["answers"]["text"][0]
    original_answer_start = line["answers"]["answer_start"][0] 
    original_answer_list = [token.text for token in list(Sentence(original_answer))]

    index = find_start_position(original_answer, line["POS_context"], original_answer_start, line["context"])
    found_answer = [list(token.values())[0][0] for token in line['POS_context'][index:index+len(original_answer_list)]]

    original_answer_list = [token.text for token in list(Sentence(original_answer + "."))[:-1]]

    #print(original_answer_list, found_answer, index, line["context"])
    
    """
    Get spans of continuous indices
    """
    # get tokens
    tokens = [list(token.values())[0][0] for token in line["POS_context"]]

    continuous_spans_indices = [
        list(map(itemgetter(1), g))
        for _, g in groupby(
            enumerate([int(list(token.keys())[0]) for token in line["NER_context"]]),
            lambda i_x: i_x[0] - i_x[1],
        )
    ]

    token_index_pos_map = {int(list(token.keys())[0]):index for index, token in enumerate(line["NER_context"])}


    """
    Insert NE tags and find the new start index for answer
    """
    updated_context = []
    span_index = 0
    token_index = 0
    new_index = 0
    initial_token_index = 0

    while token_index < len(tokens):
        #print(token_index, len(tokens))
        try:
            continuous_spans_indices[span_index][0]
        except:
            updated_context.append(tokens[token_index])
            if initial_token_index == index:
                #print("found on else")
                new_index = len(updated_context) - 1

            token_index += 1
            initial_token_index += 1
            continue

        if token_index + 1 > continuous_spans_indices[span_index][0] and len(continuous_spans_indices[span_index]) == 1:
            ne_tags = [tag[1] for tag in list(line["NER_context"][token_index_pos_map[token_index]].values())[0]]

            for ne_tag in ne_tags:
                updated_context.append("[" + ne_tag + "]")

            updated_context.append(tokens[token_index])

            if initial_token_index == index:
                #print("found one ner")
                
                if updated_context[-1][0] == "[" and updated_context[-1][-1] == "]":
                    new_index = len(updated_context) - 1 - len(ne_tags)
                else:
                    new_index = len(updated_context) - 1

            for ne_tag in ne_tags[::-1]:
                updated_context.append("[" + ne_tag + "]")

            span_index += 1
            token_index += 1
            initial_token_index += 1


        elif token_index + 1 > continuous_spans_indices[span_index][0] and len(continuous_spans_indices[span_index]) > 1:
            ne_tags = [tag[1] for tag in list(line["NER_context"][token_index_pos_map[token_index]].values())[0]]

            for ne_tag in ne_tags:
                updated_context.append("[" + ne_tag + "]")

            for i in range(len(continuous_spans_indices[span_index])):
                updated_context.append(tokens[token_index])

                if initial_token_index == index:
                    #print("found more ner")

                    if updated_context[-1][0] == "[" and updated_context[-1][-1] == "]":
                        new_index = len(updated_context) - 1 - len(ne_tags)
                    else:
                        new_index = len(updated_context) - 1

                token_index += 1
                initial_token_index += 1

            for ne_tag in ne_tags[::-1]:
                updated_context.append("[" + ne_tag + "]")

            span_index += 1

        else:
            updated_context.append(tokens[token_index])
            if initial_token_index == index:
                #print("found on else")
                new_index = len(updated_context) - 1

            token_index += 1
            initial_token_index += 1

        if token_index == len(tokens) - 1:
            updated_context.append(tokens[token_index])
            if initial_token_index == index:
                #print("found at the end")
                new_index = len(updated_context) - 1

    print(tokens[index:index+len(original_answer_list)])
    print(updated_context[new_index:new_index+10])
    print(updated_context[new_index-2:new_index+10])
    print("")

0it [00:00, ?it/s]

48it [00:00, 477.10it/s]

['Saint', 'Bernadette', 'Soubirous']
['Saint', '[PER]', 'Bernadette', 'Soubirous', '[PER]', 'in', '1858', '.', 'At', 'the']
['appeared', 'to', 'Saint', '[PER]', 'Bernadette', 'Soubirous', '[PER]', 'in', '1858', '.', 'At', 'the']

['a', 'copper', 'statue', 'of', 'Christ']
['a', 'copper', 'statue', 'of', '[PER]', 'Christ', '[PER]', 'with', 'arms', 'upraised']
[',', 'is', 'a', 'copper', 'statue', 'of', '[PER]', 'Christ', '[PER]', 'with', 'arms', 'upraised']

['the', 'Main', 'Building']
['the', '[LOC]', 'Main', 'Building', '[LOC]', "'s", 'gold', 'dome', 'is', 'a']
['.', 'Atop', 'the', '[LOC]', 'Main', 'Building', '[LOC]', "'s", 'gold', 'dome', 'is', 'a']

['a', 'Marian', 'place', 'of', 'prayer', 'and', 'reflection']
['a', '[MISC]', 'Marian', '[MISC]', 'place', 'of', 'prayer', 'and', 'reflection', '.']
['[MISC]', ',', 'a', '[MISC]', 'Marian', '[MISC]', 'place', 'of', 'prayer', 'and', 'reflection', '.']

['a', 'golden', 'statue', 'of', 'the', 'Virgin', 'Mary']
['a', 'golden', 'statue', 'of',

139it [00:00, 392.30it/s]

['Rev', '.', 'William', 'Corby']
['Rev', '.', '[PER]', 'William', 'Corby', '[PER]', ',', 'immediately', 'planned', 'for']
[',', 'the', 'Rev', '.', '[PER]', 'William', 'Corby', '[PER]', ',', 'immediately', 'planned', 'for']

['17th', 'of', 'May']
['17th', 'of', 'May', 'and', 'by', 'the', 'incredible', 'zeal', 'of', 'administrator']
['on', 'the', '17th', 'of', 'May', 'and', 'by', 'the', 'incredible', 'zeal', 'of', 'administrator']

['LaFortune', 'Student', 'Center']
['LaFortune', 'Student', 'Center', '[LOC]', '[ORG]', ')', 'was', 'built', 'in', '1883']
['[ORG]', '[LOC]', 'LaFortune', 'Student', 'Center', '[LOC]', '[ORG]', ')', 'was', 'built', 'in', '1883']

['scholastic', 'and', 'classical']
['scholastic', 'and', 'classical', 'emphasis', '.', 'By', 'contrast', ',', 'the', '[MISC]']
["'s", 'traditional', 'scholastic', 'and', 'classical', 'emphasis', '.', 'By', 'contrast', ',', 'the', '[MISC]']

['College', 'of', 'Commerce']
['College', 'of', 'Commerce', '[ORG]', ',', '[ORG]', '[PER]', '[L

...

19104it [00:25, 723.84it/s]

['Henry', 'VI']
['Henry', 'VI', '[PER]', ',', 'granted', 'on', '9', 'March', '1446', '/']
['of', '[PER]', 'Henry', 'VI', '[PER]', ',', 'granted', 'on', '9', 'March', '1446', '/']

['29', 'June', '1199']
['29', 'June', '1199', '.', 'The', 'definition', 'of', 'the', 'port', 'of']
['[LOC]', 'on', '29', 'June', '1199', '.', 'The', 'definition', 'of', 'the', 'port', 'of']

['Charles', 'I']
['Charles', 'I', '[PER]', 'by', 'at', 'once', 'the', 'formal', 'separation', 'from']
['of', '[PER]', 'Charles', 'I', '[PER]', 'by', 'at', 'once', 'the', 'formal', 'separation', 'from']

['1640']
['1640', 'the', 'formal', 'title', 'of', 'the', 'town', 'became', "'", '[LOC]']
['27', 'June', '1640', 'the', 'formal', 'title', 'of', 'the', 'town', 'became', "'", '[LOC]']

['Victorian', 'period']
['Victorian', '[MISC]', 'period', 'which', 'from', 'about', '1888', 'saw', 'the', 'setting']
['later', '[MISC]', 'Victorian', '[MISC]', 'period', 'which', 'from', 'about', '1888', 'saw', 'the', 'setting']

['Hampshire'

19351it [00:26, 741.79it/s]

['English', 'National', 'Ballet']
['English', 'National', 'Ballet', '[ORG]', '.', 'There', 'is', 'also', 'the', '[ORG]']
['and', '[ORG]', 'English', 'National', 'Ballet', '[ORG]', '.', 'There', 'is', 'also', 'the', '[ORG]']

['Nuffield', 'Theatre']
['Nuffield', 'Theatre', '[ORG]', 'based', 'at', 'the', '[ORG]', 'University', 'of', 'Southampton']
['the', '[ORG]', 'Nuffield', 'Theatre', '[ORG]', 'based', 'at', 'the', '[ORG]', 'University', 'of', 'Southampton']

['The', 'Southampton', 'City', 'Art', 'Gallery']
['The', '[ORG]', 'Southampton', 'City', 'Art', 'Gallery', '[ORG]', 'at', 'the', '[LOC]']
['city', '.', 'The', '[ORG]', 'Southampton', 'City', 'Art', 'Gallery', '[ORG]', 'at', 'the', '[LOC]']

['a', 'space']
['a', 'space', '"', '.', 'A', 'space', 'also', 'run', 'the', 'Art']
['organisation', '"', 'a', 'space', '"', '.', 'A', 'space', 'also', 'run', 'the', 'Art']

['Art', 'Vaults']
['Art', '[ORG]', 'Vaults', '[ORG]', 'project', ',', 'which', 'creatively', 'uses', 'several']
['run', 't

KeyboardInterrupt: 

In [269]:
errors

39963

In [211]:
    """
    Find last index of answer in the updated context
    """
    new_last_index = new_index
    searched_answer = copy.deepcopy(original_answer_list)
    #print(index, new_index)
    #print(updated_context)
    #print(searched_answer)
    #print(updated_context[new_index:new_index+10])

    searching_answer_iter = -1

    while len(searched_answer) != 0 or (updated_context[new_last_index] in NER_TAGS):
        #print(searched_answer)
        searching_answer_iter += 1
        if len(searched_answer) != 0:
            if searched_answer[0] in updated_context[new_last_index]:
                searched_answer.pop(0)
                new_last_index += 1

        try:
            if updated_context[new_last_index] in NER_TAGS:
                new_last_index += 1
        except:
            pass
            
        if new_last_index == len(updated_context) or searching_answer_iter == 100:
            break

    original_answer = tokens[index:index+len(original_answer_list)]
    updated_answer = updated_context[new_index:new_last_index]
    #print(original_answer, updated_answer)

    """
    Count how many errors we have
    """
    if original_answer != [token for token in updated_answer if token[0] not in NER_TAGS]:
        errors +=1

0

In [17]:
special_characters = ["$", ",", "''", "-LRB-", "-RRB-", ".", ":", "``"]


def get_proc_pos_between_item(pos_context, context, answers):
    positions = {}
    copy_answer = []
    i = 0
    # answers["answer_start"].sort()
    # answers["answer_start"].sort()
    
    for answer in answers["answer_start"]:
        answer_position = find_start_position(answers["text"][i], pos_context, answer, context)
        if answer_position != -1:
            positions[answer_position] = answers["answer_start"][i]
            copy_answer.append(answers["answer_start"][i])
        i += 1
    pos = ""
    offset = 0
    offsets = {}
    # print(positions)
    for index in range(len(pos_context)):
        pos_text = pos_context[index][str(index)]

        if pos_text[1] in special_characters:
            pos_text[1] = "sym"
        if index in positions.keys():
            offsets[positions[index]] = offset
        pos += f"{pos_text[0]} [{pos_text[1].lower()}] "
        offset += len(f" [{pos_text[1]}] ")

    answer_starts = []
    # print(copy_answer)
    for index in range(len(copy_answer)):
        answer = copy_answer[index]
        if answer == 0:
            answer_starts.append(answer)
            continue
        spaces_no = context[:answer].count(" ") + 1
        if answer not in offsets.keys():
            continue
        else:
            answer += offsets[answer] - spaces_no
        if pos[answer : answer + 1] == " ":
            answer += 1
        # if len(answers["text"]) > index:
        #     if len(answers["text"][index]) > 1:
        #         if pos[answer][0] == answers["text"][index][1]:
        #             answer -= 1
        answer_starts.append(answer)

    return pos, answer_starts


In [402]:
example_id = 84

pos, answer_starts = get_proc_pos_between_item(data[example_id]['POS_context'], data[example_id]['context'],
                          data[example_id]['answers'])
pos, answer_starts

('The [dt] university [nn] is [vbz] affiliated [vbn] with [in] the [dt] Congregation [nnp] of [in] Holy [nnp] Cross [nnp] ( [sym] Latin [nnp] : [sym] Congregatio [nnp] a [dt] Sancta [nnp] Cruce [nnp] , [sym] abbreviated [vbn] postnominals [nns] : [sym] " [sym] CSC [nnp] ") [sym] . [sym] While [in] religious [jj] affiliation [nn] is [vbz] not [rb] a [dt] criterion [nn] for [in] admission [nn] , [sym] more [jjr] than [in] 93 [cd] % [nn] of [in] students [nns] identify [vbp] as [in] Christian [nnp] , [sym] with [in] over [in] 80 [cd] % [nn] of [in] the [dt] total [nn] being [vbg] Catholic [jj] . [sym] Collectively [rb] , [sym] Catholic [nnp] Mass [nnp] is [vbz] celebrated [vbn] over [in] 100 [cd] times [nns] per [in] week [nn] on [in] campus [nn] , [sym] and [cc] a [dt] large [jj] campus [nn] ministry [nn] program [nn] provides [vbz] for [in] the [dt] faith [nn] needs [nns] of [in] the [dt] community [nn] . [sym] There [ex] are [vbp] multitudes [nns] of [in] religious [jj] statues [nns] a

In [403]:
pos[554:]

'[dt] total [nn] being [vbg] Catholic [jj] . [sym] Collectively [rb] , [sym] Catholic [nnp] Mass [nnp] is [vbz] celebrated [vbn] over [in] 100 [cd] times [nns] per [in] week [nn] on [in] campus [nn] , [sym] and [cc] a [dt] large [jj] campus [nn] ministry [nn] program [nn] provides [vbz] for [in] the [dt] faith [nn] needs [nns] of [in] the [dt] community [nn] . [sym] There [ex] are [vbp] multitudes [nns] of [in] religious [jj] statues [nns] and [cc] artwork [nn] around [in] campus [nn] , [sym] most [rbs] prominent [jj] of [in] which [wdt] are [vbp] the [dt] statue [nn] of [in] Mary [nnp] on [in] the [dt] Main [nnp] Building [nnp] , [sym] the [dt] Notre [nnp] Dame [nnp] Grotto [nnp] , [sym] and [cc] the [dt] Word [nnp] of [in] Life [nnp] mural [nn] on [in] Hesburgh [nnp] Library [nnp] depicting [vbg] Christ [nnp] as [in] a [dt] teacher [nn] . [sym] Additionally [rb] , [sym] every [dt] classroom [nn] displays [vbz] a [dt] crucifix [nn] . [sym] There [ex] are [vbp] many [jj] religious [jj]

In [404]:
for item in tqdm.tqdm(data):
    context = item['context']
    question = item['question']
    item['context'], item['answers']['answer_start'] = get_proc_pos_between_item(item['POS_context'], context, item['answers'])

    item.pop('POS_context', None)
    item.pop('POS_question', None)
    item.pop('NER_question', None)
    item.pop('NER_context', None)

100%|██████████| 87599/87599 [01:00<00:00, 1458.73it/s]


In [405]:
incorrect_answers_no = 0

for index, line in tqdm.tqdm(enumerate(data)):
    try:
        if len(line["answers"]["answer_start"]) == 0:
            continue
        answer_start = line["answers"]["answer_start"][0]
        answer = line["answers"]["text"][0]

        if answer_start == -1:
            continue

        if line["context"][answer_start:][0] != answer[0]:
            # line["answers"]["answer_start"][0] -= 1
            incorrect_answers_no += 1
            #print(index, line["context"][answer_start:], 4*'-', answer, answer_start)

    except Exception as e: 
        print(e)

87599it [00:00, 183267.93it/s]


In [406]:
incorrect_answers_no = 0

for i, line in tqdm.tqdm(enumerate(data)):
    try:
        if(len(line["answers"]["answer_start"]) == 0):
            line["answers"]["answer_start"].append(0)
        answer_start = line["answers"]["answer_start"][0]
        answer =  line["answers"]["text"][0]
        answer_length = len(answer)

        if line["context"][answer_start:][0] != answer[0]:
            incorrect_answers_no += 1

    except Exception as e: 
        # print(e)
        incorrect_answers_no += 1
        # print(i, answer_start, line["context"][answer_start:], 4*'-', answer)

87599it [00:00, 270431.26it/s]


In [407]:
data[292]

{'id': '56bf6e823aeaaa14008c9627',
 'title': 'Beyoncé',
 'context': 'Following [vbg] the [dt] disbandment [nn] of [in] Destiny [nnp] \'s [pos] Child [nnp] in [in] June [nnp] 2005 [cd] , [sym] she [prp] released [vbd] her [prp$] second [jj] solo [jj] album [nn] , [sym] B\'Day [nnp] ( [sym] 2006 [cd] ) [sym] , [sym] which [wdt] contained [vbd] hits [nns] " [sym] Déjà [nnp] Vu [nnp] " [sym] , [sym] " [sym] Irreplaceable [nnp] " [sym] , [sym] and [cc] " [sym] Beautiful [nnp] Liar [nnp] " [sym] . [sym] Beyoncé [nnp] also [rb] ventured [vbd] into [in] acting [nn] , [sym] with [in] a [dt] Golden [nnp] Globe-nominated [nnp] performance [nn] in [in] Dreamgirls [nnps] ( [sym] 2006 [cd] ) [sym] , [sym] and [cc] starring [vbg] roles [nns] in [in] The [dt] Pink [nnp] Panther [nnp] ( [sym] 2006 [cd] ) [sym] and [cc] Obsessed [nnp] ( [sym] 2009 [cd] ) [sym] . [sym] Her [prp$] marriage [nn] to [in] rapper [nn] Jay [nnp] Z [nnp] and [cc] portrayal [nn] of [in] Etta [nnp] James [nnp] in [in] Cadillac [n

In [408]:
incorrect_answers_no

2390

In [409]:
write_data("./squad_data_validation_pos_between.json", data)

Data with 'Test' property added has been saved to ./squad_data_validation_pos_between.json


In [410]:
proc_data = read_data('./squad_data_validation_pos_between.json')

In [411]:
def rreplace(string, substring, replacement):
    k = string.rfind(substring)
    return string[:k] + replacement + string[k+len(substring):]

In [412]:
symbols = ["'", '.', ',', ')']


def get_updated_answer(context, answers):
    new_answers = []
    if len(answers['answer_start']) == 0:
        return

    for index, answer in enumerate(answers['text']):
        new_answer = ''
        if len(answers['answer_start']) < index + 1:
            return new_answers
        answer_start = answers['answer_start'][index]
        if answer_start != -1:
            tokenized_context = Sentence(context[answer_start:])
            no_of_words = len(Sentence(answer))
            max_length = no_of_words * 3 + no_of_words
            if max_length > len(tokenized_context):
                max_length = len(tokenized_context)
            minus_words = 0
            for token_index in range(max_length):
                # if token_index == max_length - minus_words - 1:
                #     break
                if (tokenized_context[token_index].text == '[' and tokenized_context[token_index+1].text != '[') or (len(tokenized_context) > token_index+1 and tokenized_context[token_index].text!=']' and tokenized_context[token_index+1].text==']') or token_index == no_of_words * 4 - 1:
                    new_answer += tokenized_context[token_index].text
                elif tokenized_context[token_index].text in symbols and tokenized_context[token_index+1].text != '[':
                    new_answer += tokenized_context[token_index].text
                elif (tokenized_context[token_index].text.replace('.', '').isalpha() or tokenized_context[token_index].text[-1] in '."') and tokenized_context[token_index+1].text in '.$]':
                    new_answer += tokenized_context[token_index].text
                    # minus_words += 1
                elif len(tokenized_context) > token_index+1 and tokenized_context[token_index].text.replace('.', '').isnumeric() and tokenized_context[token_index+1].text in '.$]':
                    new_answer += tokenized_context[token_index].text
                elif tokenized_context[token_index].text.replace('-', '').isalpha() and tokenized_context[token_index+1].text in '.$]':
                    new_answer += tokenized_context[token_index].text
                elif len(tokenized_context) > token_index+1 and tokenized_context[token_index+1].text[0].isnumeric() and tokenized_context[token_index].text in '-':
                    new_answer += tokenized_context[token_index].text
                else:
                    new_answer += tokenized_context[token_index].text + ' '
        new_answer = new_answer.rstrip()
        if answer_start != -1:
            tokens_new_answer = Sentence(new_answer)
            # print(tokens_new_answer[-2])
            if tokens_new_answer[-2].text == '[':
                # print(tokens_new_answer[-2])
                new_answer += ']'
            if tokens_new_answer[-1].text == '[':
                #print(tokens_new_answer[-1], tokens_new_answer[-2].text)
                new_answer = rreplace(new_answer, tokens_new_answer[-1].text, '')
                new_answer = rreplace(new_answer, tokens_new_answer[-2].text, '')
                new_answer = new_answer.rstrip()
        new_answers.append(new_answer)
    return new_answers

In [413]:
example_id = 4892

In [414]:
get_updated_answer(proc_data[example_id]['context'], proc_data[example_id]['answers'])

['a [dt] U.S. [nnp] inventor [nn] , [sym] engineer [nn] and [cc] solar [jj] energy [nn] pioneer [nn]']

In [ ]:
for item in tqdm.tqdm(proc_data):
    item['answers']['text'] = get_updated_answer(item['context'], item['answers'])

 93%|█████████▎| 81573/87599 [03:34<00:16, 362.93it/s]

In [391]:
incorrect_answers_no = 0

for index, line in tqdm.tqdm(enumerate(proc_data)):
    try:
        if len(line["answers"]["text"]) == 0:
            line["answers"]["text"] = ['']
        if len(line["answers"]["answer_start"]) == 0:
            line["answers"]["text"] = [0]
        answer_start = line["answers"]["answer_start"][0]
        answer = line["answers"]["text"][0]
        answer_length = len(answer)

        if answer_start == -1:
            continue

        if line["context"][answer_start: answer_start + answer_length] != answer:
            incorrect_answers_no += 1
            print(index, line["context"][answer_start: answer_start + answer_length],
                  "-" * 4, answer)

        # if answer[-1] != ']':
        #     print(index, line["context"][answer_start: answer_start + answer_length], "-" * 4, answer)
        #     incorrect_answers_no += 1

    except Exception as e: 
        print(e)

10570it [00:00, 284819.05it/s]

717 :28 [cd]  ---- : 28 [cd]
3615 oxygen-18. [nn]  ---- oxygen-18 . [nn]
4006 -Gemini [jj]  ---- - Gemini [jj]


In [392]:
incorrect_answers_no / len(proc_data) * 100

0.028382213812677387

In [393]:
write_data("./squad_data_train_pos_ner_answer_updated.json", proc_data)

Data with 'Test' property added has been saved to ./squad_data_validation_pos_ner_answer_updated.json
